# Smolagents

In [73]:
from dotenv import load_dotenv, find_dotenv
import requests
import logging
from pprint import pprint

In [75]:
_ = load_dotenv(find_dotenv(raise_error_if_not_found=True), override=True)

In [28]:
DEFAULT_API_URL = "https://agents-course-unit4-scoring.hf.space"
api_url = DEFAULT_API_URL
questions_url = f"{api_url}/questions"
submit_url = f"{api_url}/submit"
task_id = 1
files_url = f"{api_url}/files/{task_id}"

In [4]:
logging.basicConfig(level=logging.INFO)
logger = logging.getLogger(__name__)

In [5]:
logger.info(f"Fetching questions from: {questions_url}")
def fetch_all_questions():
    try:
        response = requests.get(questions_url, timeout=15)
        response.raise_for_status()
        questions_data = response.json()
        if not questions_data:
             logger.info("Fetched questions list is empty.")
             return "Fetched questions list is empty or invalid format.", None
        logger.info(f"Fetched {len(questions_data)} questions.")
        return questions_data
    except requests.exceptions.RequestException as e:
        logger.info(f"Error fetching questions: {e}")
        return f"Error fetching questions: {e}", None
    except requests.exceptions.JSONDecodeError as e:
         logger.info(f"Error decoding JSON response from questions endpoint: {e}")
         logger.info(f"Response text: {response.text[:500]}")
         return f"Error decoding server response for questions: {e}", None
    except Exception as e:
        logger.info(f"An unexpected error occurred fetching questions: {e}")
        return f"An unexpected error occurred fetching questions: {e}", None
        

INFO:__main__:Fetching questions from: https://agents-course-unit4-scoring.hf.space/questions


In [6]:
all_questions = fetch_all_questions()

INFO:__main__:Fetched 20 questions.


In [3]:
import pickle

In [4]:
# with open("all_questions.pkl", "wb") as f:
#     pickle.dump(all_questions, file=f, protocol=pickle.HIGHEST_PROTOCOL)

In [5]:
with open("all_questions.pkl", "rb") as f:
    all_questions = pickle.load(f)

In [6]:
all_questions[0]

{'task_id': '8e867cd7-cff9-4e6c-867a-ff5ddc2550be',
 'question': 'How many studio albums were published by Mercedes Sosa between 2000 and 2009 (included)? You can use the latest 2022 version of english wikipedia.',
 'Level': '1',
 'file_name': ''}

In [49]:
from typing import Optional

def download_file(url: str, save_as: Optional[str] = None) -> None:
    """
    Download a file from a given URL and save it locally with the correct extension.
    
    Args:
        url (str): The URL to fetch the file.
        save_as (Optional[str]): Optional custom filename. If None, filename is extracted from headers.
    
    Returns:
        None
    """
    files_list=set(map(lambda x: str(x.stem),Path.cwd().iterdir()))
    file_name = Path(url).stem
    if file_name in files_list:
        return f"File: {file_name} already exists."
    
    response = requests.get(url, stream=True)
    
    if response.status_code == 200:
        # Extract filename from Content-Disposition header if available
        content_disposition = response.headers.get("Content-Disposition")
        if content_disposition:
            filename = content_disposition.split("filename=")[-1].strip('"')
        else:
            # Extract extension from Content-Type header
            content_type = response.headers.get("Content-Type", "application/octet-stream")
            extension = content_type.split("/")[-1]
            filename = f"downloaded_file.{extension}"
        
        # Use custom filename if provided
        if save_as:
            filename = save_as
        
        # Save the file locally
        with open(filename, "wb") as file:
            for chunk in response.iter_content(chunk_size=8192):
                file.write(chunk)
        
        print(f"File downloaded successfully: {filename}")
    else:
        print(f"Failed to download file. HTTP Status: {response.status_code}")


In [50]:

# # Example usage
# file_url = "https://agents-course-unit4-scoring.hf.space/files/99c9cc74-fdc8-46c6-8f8d-3ce2d3bfeea3"
# download_file(file_url)


In [51]:
# Path("'cca530fc-4052-43b2-b130-b30968d8aa44.png'").stem

In [52]:
# files_to_download = [i['file_name'] for i in all_questions if i['file_name']]
# for f in files_to_download:
#     file_url = f"https://agents-course-unit4-scoring.hf.space/files/{Path(f).stem}"
#     download_file(url=file_url)

In [53]:
# from smolagents import AgentAudio, AgentImage

In [54]:
# AgentAudio("99c9cc74-fdc8-46c6-8f8d-3ce2d3bfeea3.mp3").to_raw()

In [55]:
# AgentImage("cca530fc-4052-43b2-b130-b30968d8aa44.png")

In [57]:
# stt_tool("99c9cc74-fdc8-46c6-8f8d-3ce2d3bfeea3.mp3")

In [58]:
class HFImageDescriptionTool(Tool):
    name = "image_description"
    description = """
    This tool uses a Hugging Face vision-language model to describe the content of an image.
    It returns a detailed description of the provided image file.
    """
    inputs = {
        "image_path": {
            "type": "string",
            "description": "Path to the image file to be described.",
        }
    }
    output_type = "string"

    def forward(self, image_path: str) -> str:
        from huggingface_hub import InferenceClient
        from PIL import Image
        import base64
        from io import BytesIO

        def encode_image_to_base64(image_path):
            image = Image.open(image_path)
            buffered = BytesIO()
            image.save(buffered, format="JPEG")
            return base64.b64encode(buffered.getvalue()).decode("utf-8")

        client = InferenceClient(
            provider="auto",
            bill_to="VitalNest",
        )
        messages = [
            {
                "role": "user",
                "content": [
                    {"type": "text", "text": "Describe this image in detail."},
                    {
                        "type": "image_url",
                        "image_url": {
                            "url": f"data:image/jpeg;base64,{
                                encode_image_to_base64(image_path=image_path)
                            }"
                        },
                    },
                ],
            }
        ]
        completion = client.chat.completions.create(
            model="Qwen/Qwen2.5-VL-7B-Instruct",
            messages=messages,
            temperature=0.1,
            max_tokens=10000,
        )
        return completion.choices[0].message.content


image_description_tool = HFImageDescriptionTool()


In [ ]:
ultimate_agent = CodeAgent(
    tools=[
        FinalAnswerTool(),
        PythonInterpreterTool(),
        VisitWebpageTool(),
        DuckDuckGoSearchTool(),
        WikipediaSearchTool(user_agent="WikiAssistant (merlin@example.com)"),
        stt_tool,
        image_description_tool,
    ],
    additional_authorized_imports=["os", "json", "pandas", "PIL"],
    model=InferenceClientModel(
        # model_id="Qwen/Qwen3-30B-A3B",
        # model_id="Qwen/Qwen3-235B-A22B",
        bill_to="VitalNest",
        temperature=0.1,
    ),
    max_steps=10,
    planning_interval=2,
    verbosity_level=0,
    add_base_tools=True,
    name="Versatile_Multi_Agent",
    description="""You are a general AI assistant.""",
)

INFO:wikipediaapi:Wikipedia: language=en, user_agent: WikiAssistant (merlin@example.com) (Wikipedia-API/0.8.1; https://github.com/martin-majlis/Wikipedia-API/), extract_format=1


ultimate_agent.prompt_templates["system_prompt"] = ultimate_agent.prompt_templates["system_prompt"][:8834] + """
\n\n\n ALWAYS follow this ```Answer format```:\nALWAYS Report your thoughts, and finish your answer with the following template:\nANSWER: [YOUR ANSWER].\nYOUR ANSWER should be a number OR as few words as possible OR a comma separated list of numbers and/or strings.\nIf you are asked for a number, don't use comma to write your number neither use units such as $ or percent sign unless specified otherwise. If you are asked for a string, don't use articles, neither abbreviations(e.g. for cities), and write the digits in plain text unless specified otherwise.\nIf you are asked for a comma separated list, apply the above rules depending of whether the element to be put in the list is a number or a string.\n\nNow Begin!
"""

ultimate_agent.system_prompt = ultimate_agent.initialize_system_prompt()

pprint(ultimate_agent.system_prompt)

In [83]:
custom_instructions = """
\n\n\n ALWAYS follow this ```Answer format```:\nALWAYS Report your thoughts, and finish your answer with the following template:\nANSWER: [YOUR ANSWER].\nYOUR ANSWER should be a number OR as few words as possible OR a comma separated list of numbers and/or strings.\nIf you are asked for a number, don't use comma to write your number neither use units such as $ or percent sign unless specified otherwise. If you are asked for a string, don't use articles, neither abbreviations(e.g. for cities), and write the digits in plain text unless specified otherwise.\nIf you are asked for a comma separated list, apply the above rules depending of whether the element to be put in the list is a number or a string.
"""

# Set in pre_messages (recommended, so it's always seen by the model before answering)
ultimate_agent.prompt_templates["final_answer"]["pre_messages"] = custom_instructions


In [84]:
curr_task = [i for i in all_questions if i['task_id']=='1f975693-876d-457b-a649-393859e79bf3']

In [85]:
curr_task

[{'task_id': '1f975693-876d-457b-a649-393859e79bf3',
  'question': "Hi, I was out sick from my classes on Friday, so I'm trying to figure out what I need to study for my Calculus mid-term next week. My friend from class sent me an audio recording of Professor Willowbrook giving out the recommended reading for the test, but my headphones are broken :(\n\nCould you please listen to the recording for me and tell me the page numbers I'm supposed to go over? I've attached a file called Homework.mp3 that has the recording. Please provide just the page numbers as a comma-delimited list. And please provide the list in ascending order.",
  'Level': '1',
  'file_name': '1f975693-876d-457b-a649-393859e79bf3.mp3'}]

In [ ]:
ultimate_agent.run(task=curr_task[0]['question'] + "If there's a valid file_url, then the file is saved locally by the same name as the file_url."
"Only the file_url should be provided to tools as a string: 'xyz.filename' solely without any additional args or kwargs.",
                  additional_args={"file_url":f'{curr_task[0]['file_name']}'} if curr_task[0]['file_name'] else None
)
# ultimate_agent.run(task=all_questions[1]['question'] + "If there's a valid file_url, then the file is saved locally by the same name as the file_url.",
#                   additional_args={"file_url":f'{all_questions[1]['file_name']}'} if all_questions[1]['file_name'] else None
# )

In [26]:
all_questions[:]

[{'task_id': '8e867cd7-cff9-4e6c-867a-ff5ddc2550be',
  'question': 'How many studio albums were published by Mercedes Sosa between 2000 and 2009 (included)? You can use the latest 2022 version of english wikipedia.',
  'Level': '1',
  'file_name': ''},
 {'task_id': 'a1e91b78-d3d8-4675-bb8d-62741b4b68a6',
  'question': 'In the video https://www.youtube.com/watch?v=L1vXCYZAYYM, what is the highest number of bird species to be on camera simultaneously?',
  'Level': '1',
  'file_name': ''},
 {'task_id': '2d83110e-a098-4ebb-9987-066c06fa42d0',
  'question': '.rewsna eht sa "tfel" drow eht fo etisoppo eht etirw ,ecnetnes siht dnatsrednu uoy fI',
  'Level': '1',
  'file_name': ''},
 {'task_id': 'cca530fc-4052-43b2-b130-b30968d8aa44',
  'question': "Review the chess position provided in the image. It is black's turn. Provide the correct next move for black which guarantees a win. Please provide your response in algebraic notation.",
  'Level': '1',
  'file_name': 'cca530fc-4052-43b2-b130-b3096

## Inference client

In [31]:
from huggingface_hub import InferenceClient

In [32]:
client = InferenceClient(
            provider="auto",
            # provider="hyperbolic",
            bill_to="VitalNest",
)


In [38]:
from PIL import Image
import base64
from io import BytesIO

In [ ]:
_ = encode_image_to_base64("cca530fc-4052-43b2-b130-b30968d8aa44.png")

In [ ]:
def encode_image_to_base64( image_path):
    """
    Encodes an image file to a base64 string.

    Args:
        image_path (str): Path to the image file.

    Returns:
        str: Base64 encoded image string.
    """
    """Encodes a PIL image to a base64 string."""
    image = Image.open(image_path)
    buffered = BytesIO()
    image.save(buffered, format="JPEG")
    return base64.b64encode(buffered.getvalue()).decode("utf-8")


In [ ]:
messages = [
    {
        "role": "user",
        "content": [
            {"type": "text", "text": "Describe this image in detail."},
            {
                "type": "image_url",
                "image_url": {
                    "url": f"data:image/jpeg;base64,{encode_image_to_base64("cca530fc-4052-43b2-b130-b30968d8aa44.png")}"
                },
            },
        ],
    }
]
completion = client.chat.completions.create(
    model="Qwen/Qwen2.5-VL-7B-Instruct",
    messages=messages,
    temperature=0.1,
    max_tokens=10_000,
)
answer = completion.choices[0].message.content

'The image depicts a chessboard with the pieces arranged in a specific position. Here is a detailed description:\n\n1. **White Pieces:**\n   - The white king is located at the top left corner of the board, on the h-file.\n   - The white queen is not visible in this image.\n   - The white rook is on the e-file, on the e5 square.\n   - The white knight is on the d-file, on the d5 square.\n   - The white bishop is on the c-file, on the c4 square.\n   - The white rook is on the a-file, on the a2 square.\n   - The white pawn is on the a-file, on the a7 square.\n   - The white pawn is on the b-file, on the b7 square.\n   - The white pawn is on the c-file, on the c7 square.\n   - The white pawn is on the d-file, on the d7 square.\n   - The white pawn is on the e-file, on the e7 square.\n   - The white pawn is on the f-file, on the f7 square.\n   - The white pawn is on the g-file, on the g7 square.\n   - The white pawn is on the h-file, on the h7 square.\n\n2. **Black Pieces:**\n   - The black

In [46]:
pprint(answer)

('The image depicts a chessboard with the pieces arranged in a specific '
 'position. Here is a detailed description:\n'
 '\n'
 '1. **White Pieces:**\n'
 '   - The white king is located at the top left corner of the board, on the '
 'h-file.\n'
 '   - The white queen is not visible in this image.\n'
 '   - The white rook is on the e-file, on the e5 square.\n'
 '   - The white knight is on the d-file, on the d5 square.\n'
 '   - The white bishop is on the c-file, on the c4 square.\n'
 '   - The white rook is on the a-file, on the a2 square.\n'
 '   - The white pawn is on the a-file, on the a7 square.\n'
 '   - The white pawn is on the b-file, on the b7 square.\n'
 '   - The white pawn is on the c-file, on the c7 square.\n'
 '   - The white pawn is on the d-file, on the d7 square.\n'
 '   - The white pawn is on the e-file, on the e7 square.\n'
 '   - The white pawn is on the f-file, on the f7 square.\n'
 '   - The white pawn is on the g-file, on the g7 square.\n'
 '   - The white pawn is

# Async Task

In [64]:
from concurrent.futures import ThreadPoolExecutor, as_completed, ProcessPoolExecutor

In [65]:
questions = all_questions[:5]

In [66]:
all_questions[:5]

[{'task_id': '8e867cd7-cff9-4e6c-867a-ff5ddc2550be',
  'question': 'How many studio albums were published by Mercedes Sosa between 2000 and 2009 (included)? You can use the latest 2022 version of english wikipedia.',
  'Level': '1',
  'file_name': ''},
 {'task_id': 'a1e91b78-d3d8-4675-bb8d-62741b4b68a6',
  'question': 'In the video https://www.youtube.com/watch?v=L1vXCYZAYYM, what is the highest number of bird species to be on camera simultaneously?',
  'Level': '1',
  'file_name': ''},
 {'task_id': '2d83110e-a098-4ebb-9987-066c06fa42d0',
  'question': '.rewsna eht sa "tfel" drow eht fo etisoppo eht etirw ,ecnetnes siht dnatsrednu uoy fI',
  'Level': '1',
  'file_name': ''},
 {'task_id': 'cca530fc-4052-43b2-b130-b30968d8aa44',
  'question': "Review the chess position provided in the image. It is black's turn. Provide the correct next move for black which guarantees a win. Please provide your response in algebraic notation.",
  'Level': '1',
  'file_name': 'cca530fc-4052-43b2-b130-b3096

In [67]:
def run_agents_in_parallel(task, additional_args):
    res = ultimate_agent.run(task=task, additional_args=additional_args)
    return res
def process_question(q):
    task = (
        q["question"]
        + "If there's a valid file_url, then the file is saved locally by the same name as the file_url."
        "Only the file_url should be provided to tools as a string: 'xyz.filename' solely without any additional args or kwargs."
    )
    additional_args = {"file_url": f"{q['file_name']}"} if q["file_name"] else None
    return (run_agents_in_parallel(task, additional_args))

In [75]:
with ThreadPoolExecutor(max_workers=8) as executor:
    futures = {
        executor.submit(
            process_question,
            q
        ): q['question']
        for q in questions
    }
    results = {}
    for future in as_completed(futures):
        question = futures[future]
        result = future.result()
        results[question] = result



18:31:23 - LiteLLM:INFO: utils.py:3101 - 
LiteLLM completion() model= gpt-4.1; provider = openai
INFO:LiteLLM:
LiteLLM completion() model= gpt-4.1; provider = openai
18:31:23 - LiteLLM:INFO: utils.py:3101 - 
LiteLLM completion() model= gpt-4.1; provider = openai
18:31:23 - LiteLLM:INFO: utils.py:3101 - 
LiteLLM completion() model= gpt-4.1; provider = openai
INFO:LiteLLM:
LiteLLM completion() model= gpt-4.1; provider = openai
INFO:LiteLLM:
LiteLLM completion() model= gpt-4.1; provider = openai
18:31:23 - LiteLLM:INFO: utils.py:3101 - 
LiteLLM completion() model= gpt-4.1; provider = openai
INFO:LiteLLM:
LiteLLM completion() model= gpt-4.1; provider = openai
18:31:23 - LiteLLM:INFO: utils.py:3101 - 
LiteLLM completion() model= gpt-4.1; provider = openai
INFO:LiteLLM:
LiteLLM completion() model= gpt-4.1; provider = openai
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 200 OK"
18:31:37 - LiteLLM:INFO: utils.py:1215 - Wrapper: Completed Call, calling succe


Give Feedback / Get Help: https://github.com/BerriAI/litellm/issues/new
LiteLLM.Info: If you need to debug this error, use `litellm._turn_on_debug()'.



Error in generating model output:
litellm.BadRequestError: OpenAIException - Invalid value: 'tool-call'. Supported values are: 'system', 'assistant',
'user', 'function', 'tool', and 'developer'.

INFO:primp:response: https://html.duckduckgo.com/html 200
18:31:41 - LiteLLM:INFO: utils.py:3101 - 
LiteLLM completion() model= gpt-4.1; provider = openai
INFO:LiteLLM:
LiteLLM completion() model= gpt-4.1; provider = openai
INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 400 Bad Request"



Give Feedback / Get Help: https://github.com/BerriAI/litellm/issues/new
LiteLLM.Info: If you need to debug this error, use `litellm._turn_on_debug()'.



...


Give Feedback / Get Help: https://github.com/BerriAI/litellm/issues/new
LiteLLM.Info: If you need to debug this error, use `litellm._turn_on_debug()'.



INFO:httpx:HTTP Request: POST https://api.openai.com/v1/chat/completions "HTTP/1.1 400 Bad Request"



Give Feedback / Get Help: https://github.com/BerriAI/litellm/issues/new
LiteLLM.Info: If you need to debug this error, use `litellm._turn_on_debug()'.



Error in generating model output:
litellm.BadRequestError: OpenAIException - Invalid value: 'tool-call'. Supported values are: 'system', 'assistant',
'user', 'function', 'tool', and 'developer'.

AgentGenerationError: Error in generating model output:
litellm.BadRequestError: OpenAIException - Invalid value: 'tool-call'. Supported values are: 'system', 'assistant', 'user', 'function', 'tool', and 'developer'.

In [76]:
pprint(results)

{}


# Langchain

In [ ]:
from smolagents import (
    DuckDuckGoSearchTool,
    VisitWebpageTool,
    LocalPythonExecutor,
    PythonInterpreterTool,
    WikipediaSearchTool,
    Tool
)

import polars as pl
from pathlib import Path
from typing import Any
import cv2
from PIL import Image
import base64
from io import BytesIO
from langchain.chat_models import init_chat_model
from langchain_core.messages import HumanMessage
from langgraph.prebuilt import create_react_agent
from pydantic import BaseModel, Field
from langgraph.errors import GraphRecursionError
from dotenv import load_dotenv, find_dotenv
import pickle
import asyncio
import nest_asyncio

import httpx

In [2]:
_ = load_dotenv(find_dotenv(raise_error_if_not_found=True), override=True)
nest_asyncio.apply()
with open("all_questions.pkl", "rb") as f:
    all_questions = pickle.load(f)

In [56]:
lang_model = init_chat_model(model="gpt-4.1", model_provider="openai",temperature=0.2)
# lang_model = init_chat_model(model="gpt-4.1-nano", model_provider="openai",temperature=0.2)
# lang_model = init_chat_model(model="gpt-4.1-mini", model_provider="openai",temperature=0.2)

In [4]:
def search_wikipedia(query: str) -> str:
    """Tries to search for a wikipedia page relevant to the query and if it finds
    then it returns the content of this page."""
    wiki_search = WikipediaSearchTool(user_agent="WikiAssistant (merlin@example.com)")
    content = wiki_search(query)
    return content

In [5]:
def visit_web_page(url:str) -> str:
    """Use this tool to visit websites."""
    visit_webpage = VisitWebpageTool(max_output_length=60_000)
    web_content = visit_webpage(url)
    return web_content

In [6]:
def read_excel_or_csv(filepath: str) -> str:
    """Reads an excel or csv file and returns the content as str."""
    if Path(filepath).suffix in {".xlsx", ".xls"}:
        df = pl.read_excel(source=filepath)
    else:
        df = pl.read_csv(source=filepath)
    content_str = df.to_dict(as_series=False).__str__()
    return content_str


In [7]:
def python_code_interpreter(filepath: str) -> Any:
    """Returns the output of a python code."""
    with open(filepath, "r") as f:
        code = f.readlines()
    code_result = lang_model.generate(
        messages=[
            [
                HumanMessage(
                    content=[
                        {
                            "type": "text",
                            "text": f"What's the result of this code: {code}. Return only the output without any explanation.",
                        },
                    ]
                )
            ]
        ]
    )
    return code_result.generations[0][0].text

In [8]:
stt_tool = Tool.from_space(space_id="UNSAFESUPERINTELLIGENCE/Minimum-OpenAI-Whisper",
                description="Speech to Text Tool",
                name="stt_tool")

Loaded as API: https://unsafesuperintelligence-minimum-openai-whisper.hf.space ✔


Since `api_name` was not defined, it was automatically set to the first available API: `/predict`.


In [9]:
def call_stt_tool(file_url:str) -> str:
    """Speech to text tool."""
    transcribed_text = stt_tool(file_url)
    return transcribed_text

In [10]:

def encode_image_to_base64(image_path:str) -> bytes:
    image = Image.open(image_path)
    buffered = BytesIO()
    image.save(buffered, format="JPEG")
    return base64.b64encode(buffered.getvalue()).decode("utf-8")

def image_tool(file_url:str) -> str:
    """Describes an image in detail."""
    img_resp = lang_model.generate(
        messages=[
            [
                HumanMessage(
                    content=[
                        {
                            "type": "text",
                            "text": "Describe the image in detail and return only the description without any additional content.",
                        },
                        {
                            "type": "image_url",
                            "image_url": {
                                "url": f"data:image/jpeg;base64,{encode_image_to_base64(image_path=file_url)}"
                            },
                        },
                    ]
                )
            ]
        ]
    )


    return img_resp.generations[0][0].text


In [11]:
# image_tool(file_url="cca530fc-4052-43b2-b130-b30968d8aa44.png")

In [12]:
def youtube_video_tool(url:str, query:str) -> str:
    """Answers questions about youtube videos.
    URLs must be provided to this tool and the query too."""
    yt_vid_mapping = {"https://www.youtube.com/watch?v=L1vXCYZAYYM": "penguin.mp4",
                  "https://www.youtube.com/watch?v=1htKBjuUWec": "coffee.mp4"}
    video = cv2.VideoCapture(filename=yt_vid_mapping[url])

    base64Frames = []
    while video.isOpened():
        success, frame = video.read()
        if not success:
            break
        _, buffer = cv2.imencode(".jpg", frame)
        base64Frames.append(base64.b64encode(s=buffer).decode(encoding="utf-8"))

    video.release()
    vid_resp = lang_model.generate(
    messages=[
        [
            HumanMessage(
                content=[
                    {
                        "type": "text",
                        "text": (
                            f"""Examine the video and answer the following question: {query}."""
                        ),
                    },
                    *[
                        {
                            "type": "image_url",
                            "image_url": {"url":f"data:image/jpeg;base64,{frame}"},
                        }
                        for frame in base64Frames[0::25]
                    ],
                ],
            )
        ]
    ]
)
    return vid_resp.generations[0][0].text

In [13]:
def web_search_tool(query: str) -> str:
    """Use a search engine to search the web for general information."""
    ddg_tool = DuckDuckGoSearchTool(max_results=5)
    search_res = ddg_tool(query)
    return search_res

In [14]:
def python_executor(code_str:str) -> str:
    """This executes python code. The code must be a string.
    For any calculations always use numpy."""
    lpe = LocalPythonExecutor(additional_authorized_imports=['polars.*', 'numpy.*'])
    code_res = lpe(code_action=code_str)[0]
    return code_res

In [15]:
class AnswerFormat(BaseModel):
    """Pydantic model for the answer format instructions.

    Attributes:
        thoughts (str): The reasoning or thoughts before the answer.
        answer (str | int | list[str | int]): The final answer, following strict formatting rules.
    """

    thoughts: str = Field(..., description="Report your thoughts before the answer.")
    answer: str | int | list[str | int] = Field(
        ...,
        description=(
            "The answer should be a number (no commas or units), "
            "a few words (no articles or abbreviations), "
            "or a comma-separated list of numbers/strings, "
            "following all specified formatting rules."
        ),
    )


In [16]:
# SYS_PROMPT_SWEBENCH = """
# You will be tasked to fix an issue from an open-source repository.

# Your thinking should be thorough and so it's fine if it's very long. You can think step by step before and after each action you decide to take.

# You MUST iterate and keep going until the problem is solved.

# You already have everything you need to solve this problem in the /testbed folder, even without internet connection. I want you to fully solve this autonomously before coming back to me.

# Only terminate your turn when you are sure that the problem is solved. Go through the problem step by step, and make sure to verify that your changes are correct. NEVER end your turn without having solved the problem, and when you say you are going to make a tool call, make sure you ACTUALLY make the tool call, instead of ending your turn.

# THE PROBLEM CAN DEFINITELY BE SOLVED WITHOUT THE INTERNET.

# Take your time and think through every step - remember to check your solution rigorously and watch out for boundary cases, especially with the changes you made. Your solution must be perfect. If not, continue working on it. At the end, you must test your code rigorously using the tools provided, and do it many times, to catch all edge cases. If it is not robust, iterate more and make it perfect. Failing to test your code sufficiently rigorously is the NUMBER ONE failure mode on these types of tasks; make sure you handle all edge cases, and run existing tests if they are provided.

# You MUST plan extensively before each function call, and reflect extensively on the outcomes of the previous function calls. DO NOT do this entire process by making function calls only, as this can impair your ability to solve the problem and think insightfully.

# # Workflow

# ## High-Level Problem Solving Strategy

# 1. Understand the problem deeply. Carefully read the issue and think critically about what is required.
# 2. Investigate the codebase. Explore relevant files, search for key functions, and gather context.
# 3. Develop a clear, step-by-step plan. Break down the fix into manageable, incremental steps.
# 4. Implement the fix incrementally. Make small, testable code changes.
# 5. Debug as needed. Use debugging techniques to isolate and resolve issues.
# 6. Test frequently. Run tests after each change to verify correctness.
# 7. Iterate until the root cause is fixed and all tests pass.
# 8. Reflect and validate comprehensively. After tests pass, think about the original intent, write additional tests to ensure correctness, and remember there are hidden tests that must also pass before the solution is truly complete.

# Refer to the detailed sections below for more information on each step.

# ## 1. Deeply Understand the Problem
# Carefully read the issue and think hard about a plan to solve it before coding.

# ## 2. Codebase Investigation
# - Explore relevant files and directories.
# - Search for key functions, classes, or variables related to the issue.
# - Read and understand relevant code snippets.
# - Identify the root cause of the problem.
# - Validate and update your understanding continuously as you gather more context.

# ## 3. Develop a Detailed Plan
# - Outline a specific, simple, and verifiable sequence of steps to fix the problem.
# - Break down the fix into small, incremental changes.

# ## 4. Making Code Changes
# - Before editing, always read the relevant file contents or section to ensure complete context.
# - If a patch is not applied correctly, attempt to reapply it.
# - Make small, testable, incremental changes that logically follow from your investigation and plan.

# ## 5. Debugging
# - Make code changes only if you have high confidence they can solve the problem
# - When debugging, try to determine the root cause rather than addressing symptoms
# - Debug for as long as needed to identify the root cause and identify a fix
# - Use print statements, logs, or temporary code to inspect program state, including descriptive statements or error messages to understand what's happening
# - To test hypotheses, you can also add test statements or functions
# - Revisit your assumptions if unexpected behavior occurs.

# ## 6. Testing
# - Run tests frequently using `!python3 run_tests.py` (or equivalent).
# - After each change, verify correctness by running relevant tests.
# - If tests fail, analyze failures and revise your patch.
# - Write additional tests if needed to capture important behaviors or edge cases.
# - Ensure all tests pass before finalizing.

# ## 7. Final Verification
# - Confirm the root cause is fixed.
# - Review your solution for logic correctness and robustness.
# - Iterate until you are extremely confident the fix is complete and all tests pass.

# ## 8. Final Reflection and Additional Testing
# - Reflect carefully on the original intent of the user and the problem statement.
# - Think about potential edge cases or scenarios that may not be covered by existing tests.
# - Write additional tests that would need to pass to fully validate the correctness of your solution.
# - Run these new tests and ensure they all pass.
# - Be aware that there are additional hidden tests that must also pass for the solution to be successful.
# - Do not assume the task is complete just because the visible tests pass; continue refining until you are confident the fix is robust and comprehensive.
# """

# PYTHON_TOOL_DESCRIPTION = """This function is used to execute Python code or terminal commands in a stateful Jupyter notebook environment. python will respond with the output of the execution or time out after 60.0 seconds. Internet access for this session is disabled. Do not make external web requests or API calls as they will fail. Just as in a Jupyter notebook, you may also execute terminal commands by calling this function with a terminal command, prefaced with an exclamation mark.

# In addition, for the purposes of this task, you can call this function with an `apply_patch` command as input.  `apply_patch` effectively allows you to execute a diff/patch against a file, but the format of the diff specification is unique to this task, so pay careful attention to these instructions. To use the `apply_patch` command, you should pass a message of the following structure as "input":

# %%bash
# apply_patch <<"EOF"
# *** Begin Patch
# [YOUR_PATCH]
# *** End Patch
# EOF

# Where [YOUR_PATCH] is the actual content of your patch, specified in the following V4A diff format.

# *** [ACTION] File: [path/to/file] -> ACTION can be one of Add, Update, or Delete.
# For each snippet of code that needs to be changed, repeat the following:
# [context_before] -> See below for further instructions on context.
# - [old_code] -> Precede the old code with a minus sign.
# + [new_code] -> Precede the new, replacement code with a plus sign.
# [context_after] -> See below for further instructions on context.

# For instructions on [context_before] and [context_after]:
# - By default, show 3 lines of code immediately above and 3 lines immediately below each change. If a change is within 3 lines of a previous change, do NOT duplicate the first change's [context_after] lines in the second change's [context_before] lines.
# - If 3 lines of context is insufficient to uniquely identify the snippet of code within the file, use the @@ operator to indicate the class or function to which the snippet belongs. For instance, we might have:
# @@ class BaseClass
# [3 lines of pre-context]
# - [old_code]
# + [new_code]
# [3 lines of post-context]

# - If a code block is repeated so many times in a class or function such that even a single @@ statement and 3 lines of context cannot uniquely identify the snippet of code, you can use multiple `@@` statements to jump to the right context. For instance:

# @@ class BaseClass
# @@ 	def method():
# [3 lines of pre-context]
# - [old_code]
# + [new_code]
# [3 lines of post-context]

# Note, then, that we do not use line numbers in this diff format, as the context is enough to uniquely identify code. An example of a message that you might pass as "input" to this function, in order to apply a patch, is shown below.

# %%bash
# apply_patch <<"EOF"
# *** Begin Patch
# *** Update File: pygorithm/searching/binary_search.py
# @@ class BaseClass
# @@     def search():
# -        pass
# +        raise NotImplementedError()

# @@ class Subclass
# @@     def search():
# -        pass
# +        raise NotImplementedError()

# *** End Patch
# EOF

# File references can only be relative, NEVER ABSOLUTE. After the apply_patch command is run, python will always say "Done!", regardless of whether the patch was successfully applied or not. However, you can determine if there are issue and errors by looking at any warnings or logging lines printed BEFORE the "Done!" is output.
# """


In [57]:
# https://cookbook.openai.com/examples/gpt4-1_prompting_guide
SYSTEM_PROMPT = """
You are an expert agent - please keep going until the user’s query is completely resolved, before ending your turn and yielding back to the user. Only terminate your turn when you are sure that the problem is solved. 


# Instructions
- Carefully read and understand the task. Sometimes the task might be a sentence reversed, so un reverse it first and then complete the task.
- Sometimes the task will be accompanied with a file, and the file name will be provided to you. If no file is provided to you don't try looking for a file, for instance "discograpy".
- If you are not sure about file content or codebase structure pertaining to the user’s request, use your tools to read files and gather the relevant information: do NOT guess or make up an answer.
- You can use a combination of tools to complete the task, however, you don't have to use the tools all the time.
- Before using any tool always check what's the input/s that the tool expects and provide the input accordingly. Extract any necessary information from the query given to you for the tool call.
- You have access to the following tools: `search_wikipedia`, `visit_web_page`, `read_excel_or_csv`, `python_executor`, `python_code_interpreter`, `call_stt_tool`, `image_tool`, `youtube_video_tool`, `web_search_tool`.
- If a python file is given to you, then use the `python_code_interpreter` and the input to the tool should be the file name.
- For any youtube related task use the `youtube_video_tool` and the input to the tool should be URL as a string along with the query.
- For any dataframe related tasks, always use the `read_excel_or_csv` tool.
- If the `search_wikipedia` tool has provided a page, then no need to call `visit_web_page` for the same wikipedia page, instead use the content that's provided by the `search_wikipedia` tool.
- You MUST plan extensively before each tool call, and reflect extensively on the outcomes of the previous tool calls. DO NOT do this entire process by making tool calls only, as this can impair your ability to solve the problem and think insightfully.
- Always verify your answers.


#Output Format
- YOUR ANSWER should be a number OR as few words as possible OR a comma separated list of numbers and/or strings.
- If you are asked for a number, don't use comma to write your number neither use units such as $ or percent sign unless specified otherwise.
- If you are asked for a string, don't use articles, neither abbreviations(e.g. for cities), and write the digits in plain text unless specified otherwise.
- If you are asked for a comma separated list, apply the above rules depending of whether the element to be put in the list is a number or a string.
- Leverage the `AnswerFormat` pydantic class to output the answer.

# Example
## User
Examine the video at https://www.youtube.com/watch?v=1htKBjuUWec.\n\nWhat does Teal\'c say in response to the question "Isn\'t that hot?"

## Assistant
<Internal thought> First let me extract the youtube url and then use the `youtube_video_tool` to answer this query.</Internal thought>
### Tool Calls
youtube_video_tool(https://www.youtube.com/watch?v=1htKBjuUWec)

// After tool call, the assistant would follow up with the response from the tool:

<Internal thought> I need to format the tool response as per the expected output. </Internal thought>

## Assistant response
### Message
"The correct answer."

# Example 2
## User
What's 2 +2 ?

## Assistant response
### Message
4

"""

In [58]:
agent = create_react_agent(
    model=lang_model,
    tools=[
        search_wikipedia,
        visit_web_page,
        read_excel_or_csv,
        python_executor,
        python_code_interpreter,
        call_stt_tool,
        image_tool,
        youtube_video_tool,
        web_search_tool,
    ],
    prompt=SYSTEM_PROMPT,
    response_format=AnswerFormat,
)

In [42]:
# recursion_limit = 10
# agent_w_recursion_limit = agent.with_config(recursion_limit=recursion_limit)

In [43]:
all_questions[0]

{'task_id': '8e867cd7-cff9-4e6c-867a-ff5ddc2550be',
 'question': 'How many studio albums were published by Mercedes Sosa between 2000 and 2009 (included)? You can use the latest 2022 version of english wikipedia.',
 'Level': '1',
 'file_name': ''}

In [59]:
results = []
for q in all_questions:
    try:
        answer = await agent.ainvoke(
        # answer = agent_w_recursion_limit.invoke(
            input={
                "messages": f"""Complete the following task: {q["question"]}. Relevant file: {
                    q["file_name"]
                    if q["file_name"]
                    else "There's no relevant file to use."
                }"""
            }
        )
        results.append(answer)
    except GraphRecursionError:
        print("❌ Agent stopped due to max iterations.")
        results.append(q["task_id"])

❌ Agent stopped due to max iterations.


In [45]:
# [results[i]["structured_response"].answer if isinstance(results[i], dict) else "No answer" for i in range(len(all_questions))]

In [49]:
# with open("results_gpt_nano.pkl", "wb") as f:
#     pickle.dump(obj=results, file=f, protocol=pickle.HIGHEST_PROTOCOL)

In [60]:
answers = [{"task_id":j['task_id'], 
            "submitted_answer": results[i]["structured_response"].answer
            if isinstance(results[i], dict) else "No answer"} 
 for i,j in enumerate(all_questions)]

In [61]:
data = {
  "username": "string",
  "agent_code": "stringstri",
  "answers": answers
}

In [62]:
answer_check = httpx.post(json=data, url=submit_url)

In [63]:
answer_check.json()

{'username': 'string',
 'score': 30.0,
 'correct_count': 6,
 'total_attempted': 20,
 'message': 'Score calculated successfully: 6/20 total questions answered correctly (20 valid tasks attempted). Score did not improve previous record, leaderboard not updated.',
 'timestamp': '2025-06-14T12:19:54.753829+00:00'}

In [108]:
all_questions[18]

{'task_id': '7bd855d8-463d-4ed5-93ca-5fe35145f733',
 'question': 'The attached Excel file contains the sales of menu items for a local fast-food chain. What were the total sales that the chain made from food (not including drinks)? Express your answer in USD with two decimal places.',
 'Level': '1',
 'file_name': '7bd855d8-463d-4ed5-93ca-5fe35145f733.xlsx'}

In [25]:
agent.invoke(
            input={
                "messages": f"""Complete the following task: {all_questions[18]["question"]}. Relevant file: {
                    all_questions[18]["file_name"]
                    if all_questions[18]["file_name"]
                    else "There's no relevant file to use."
                }"""
            }
        )

{'messages': [HumanMessage(content='Complete the following task: The attached Excel file contains the sales of menu items for a local fast-food chain. What were the total sales that the chain made from food (not including drinks)? Express your answer in USD with two decimal places.. Relevant file: 7bd855d8-463d-4ed5-93ca-5fe35145f733.xlsx', additional_kwargs={}, response_metadata={}, id='9c810520-a1cd-40b2-914e-8fd2f3e240c5'),
  AIMessage(content='', additional_kwargs={'tool_calls': [{'id': 'call_zp8tBlFZ1vOSnYqFQvbsgbi6', 'function': {'arguments': '{"filepath":"7bd855d8-463d-4ed5-93ca-5fe35145f733.xlsx"}', 'name': 'read_excel_or_csv'}, 'type': 'function'}], 'refusal': None}, response_metadata={'token_usage': {'completion_tokens': 38, 'prompt_tokens': 1104, 'total_tokens': 1142, 'completion_tokens_details': {'accepted_prediction_tokens': 0, 'audio_tokens': 0, 'reasoning_tokens': 0, 'rejected_prediction_tokens': 0}, 'prompt_tokens_details': {'audio_tokens': 0, 'cached_tokens': 1024}}, '

In [40]:
# async def run_all_questions(agent, all_questions):
#     """Run agent.ainvoke concurrently for all questions.

#     Args:
#         agent: The LangChain agent with an ainvoke method.
#         all_questions (list): List of question dicts.

#     Returns:
#         list: List of agent responses.
#     """
#     tasks = [
#         agent.ainvoke(
#             input={
#                 "messages": f"""Complete the following task: {q["question"]}. Relevant file: {
#                     q["file_name"] if q["file_name"] else "There's no relevant file to use."
#                 }"""
#             }
#         )
#         for q in all_questions
#     ]
#     try:
#         return await asyncio.gather(*tasks)
#     except GraphRecursionError as err:
#         print("❌ Agent stopped due to max iterations.")
#         print(f"Error: {err}")
#         # return "Recursion Limit Reached."



In [ ]:
# responses = asyncio.run(run_all_questions(agent, all_questions))

In [43]:
type(responses)

NoneType

In [35]:
responses[2]['structured_response'].answer

TypeError: string indices must be integers, not 'str'

In [23]:
all_questions[2]

{'task_id': '2d83110e-a098-4ebb-9987-066c06fa42d0',
 'question': '.rewsna eht sa "tfel" drow eht fo etisoppo eht etirw ,ecnetnes siht dnatsrednu uoy fI',
 'Level': '1',
 'file_name': ''}

In [71]:
responses[19]

{'messages': [HumanMessage(content="Complete the following task: What is the first name of the only Malko Competition recipient from the 20th Century (after 1977) whose nationality on record is a country that no longer exists?. Relevant file: There's no relevant file to use.", additional_kwargs={}, response_metadata={}, id='8f1e5b86-49a8-4bf1-9cb1-3f5cc5a6aeb1'),
  AIMessage(content='', additional_kwargs={'tool_calls': [{'id': 'call_ZgHuwBfr09DQIN6it7F1tXBl', 'function': {'arguments': '{"query": "Malko Competition winners by nationality"}', 'name': 'web_search_tool'}, 'type': 'function'}, {'id': 'call_Rwe5uh7sXQL22rRFiXnjEbre', 'function': {'arguments': '{"query": "List of countries that no longer exist"}', 'name': 'web_search_tool'}, 'type': 'function'}], 'refusal': None}, response_metadata={'token_usage': {'completion_tokens': 58, 'prompt_tokens': 1013, 'total_tokens': 1071, 'completion_tokens_details': {'accepted_prediction_tokens': 0, 'audio_tokens': 0, 'reasoning_tokens': 0, 'reje